In [17]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from astropy.table import Table

from svom.utils import FitsProductFromModel
import vtac
from vtac.handler import get_product_template

from pprint import pprint
from pathlib import Path
import logging
log = logging.getLogger(__name__)
log.setLevel(logging.INFO)

In [2]:
SIM_DIR = Path('/Users/palmerio/SVOM_pipeline/VT_simulations/')

In [3]:
cases = [
    'bright_case1',
    'bright_case1a',
    'bright_case2',
    'bright_case3',
    'bright_case4',
    'faint_case1',
    'faint_case2',
    'faint_case3',
    'faint_case4',
]
sequences = ['s1', 's2', 's3', 's4']
bands = ['R', 'B']

files = {case:{seq:{band:{} for band in bands} for seq in sequences} for case in cases}

In [4]:
pprint(files)

{'bright_case1': {'s1': {'B': {}, 'R': {}},
                  's2': {'B': {}, 'R': {}},
                  's3': {'B': {}, 'R': {}},
                  's4': {'B': {}, 'R': {}}},
 'bright_case1a': {'s1': {'B': {}, 'R': {}},
                   's2': {'B': {}, 'R': {}},
                   's3': {'B': {}, 'R': {}},
                   's4': {'B': {}, 'R': {}}},
 'bright_case2': {'s1': {'B': {}, 'R': {}},
                  's2': {'B': {}, 'R': {}},
                  's3': {'B': {}, 'R': {}},
                  's4': {'B': {}, 'R': {}}},
 'bright_case3': {'s1': {'B': {}, 'R': {}},
                  's2': {'B': {}, 'R': {}},
                  's3': {'B': {}, 'R': {}},
                  's4': {'B': {}, 'R': {}}},
 'bright_case4': {'s1': {'B': {}, 'R': {}},
                  's2': {'B': {}, 'R': {}},
                  's3': {'B': {}, 'R': {}},
                  's4': {'B': {}, 'R': {}}},
 'faint_case1': {'s1': {'B': {}, 'R': {}},
                 's2': {'B': {}, 'R': {}},
                 's3': {'

## Create file paths

In [6]:
n_files_tot = 0
for case in cases:
    _dir = SIM_DIR/f"{case}/qsrclist_{case}_s1/"
    sim_ids = np.unique([f.stem.split('_')[0] for f in _dir.glob("*.dat")])
    print(f"{len(sim_ids)} different simulations for {case}")
    files[case]["sim_ids"] = sim_ids
    
    for seq in sequences:
        for band in bands:
            dir = SIM_DIR/f"{case}/qsrclist_{case}_{seq}/"
            # Get all files matching a pattern
            _files = [f for f in dir.glob(f"*_{band}.dat")]
            _files.sort()
            files[case][seq][band] = _files
            n_files_tot += len(_files)
print(f"Total number of files: {n_files_tot}")
# Simulation 71 is missing from bright_case1a, dunno why

238 different simulations for bright_case1
237 different simulations for bright_case1a
238 different simulations for bright_case2
238 different simulations for bright_case3
238 different simulations for bright_case4
238 different simulations for faint_case1
238 different simulations for faint_case2
238 different simulations for faint_case3
238 different simulations for faint_case4
Total number of files: 16625


## Create fits product

In [7]:
def read_header(fname):
    hdr = {}
    with open(fname, 'r') as f:
        for l in f.readlines():
            if l.startswith('#'):
                _split_line = l.strip().split()
                if len(_split_line) == 2:
                    key = _split_line[0]
                    val = _split_line[1]
                    hdr[key.strip("#").upper()] = val
    return hdr
    

In [8]:
def fill_headers(fits_template, keywords_dict):
    """
    Fill the headers of the various fits extensions with the
    keywords used during processing.

    Parameters
    ----------
    fits_template : FitsProductFromModel
        FitsProductFromModel whose keywords need to be updated
    keywords_dict : dict
        Dictionary whose keys are the name of the extension
        and value is a dictionary of keywords. Example:
        keywords_dict={'PrimaryHDU':{'OBS_ID':'sb12345678'},'R1':{'BAND':'VT_R'}}
    """

    # Iterate over the various fits extensions
    for ext, keywords in keywords_dict.items():
        log.debug("Processing keywords for extension '%s'" % ext)
        fits_template.update_header(keywords, ext=ext)


In [23]:
for case in cases:
    log.info(f"Processing simulations for case: {case}")
    fits_dir = SIM_DIR/f"{case}/fits"
    fits_dir.mkdir(exist_ok=True)
    i = 0
    i_tot = len(files[case]["sim_ids"])
    for sim_id in files[case]["sim_ids"]:
        log.info(50*"#")
        log.info(f"Progress: {100*i/i_tot} %")
        log.info(50*"#")
        log.info(f"Processing simulation {sim_id}")
        # Get the fits template
        qsrclist_vt = get_product_template(
            acronym="QSRCLIST_VT",
            mode="local",
            json_product_descriptor_path="/Users/palmerio/SVOM_pipeline/json-product-descriptor/",
        )
        try:
            for seq_n in sequences:
                for band in bands:
                    log.info(f"Processing sequence {seq_n} of band {band}")
                    fname = [f for f in files[case][seq_n][band] if f.stem.split('_')[0] == sim_id][0]
                    tab = Table.read(
                        fname,
                        format='ascii',
                        delimiter='\s',
                        guess=False,
                        fast_reader=False,
                        names=[
                            "id",
                            "x",
                            "y",
                            "ra",
                            "dec",
                            "mag",
                            "magerr",
                            "flag",
                            "ellipticity",
                        ]
                    )
                    tab.rename_columns(
                        (
                            "id",
                            "x",
                            "y",
                            "ra",
                            "dec",
                            "mag",
                            "magerr",
                            "flag",
                            "ellipticity",
                        ),
                        (
                            "OBJID",
                            "X",
                            "Y",
                            "RA",
                            "DEC",
                            "MAGCAL",
                            "MAGERR",
                            "EFLAG",
                            "ELLIPTY",
                        )
                    )
                    hdr = read_header(fname)
                    seq_name = "{}{}".format(hdr["BAND"][0].upper(), hdr["NTH"])
                    hdr["SIM_ID"] = fname.stem.split('_')[0]
                    hdr["SEQ"] = seq_name
                    seq = seq_name
        
                    # Add missing keywords
                    hdr["MAGLIM"] = 23.0
        
                    ext_name = f"FINDCH_{seq}"
                    log.debug(f"Filling template's '{ext_name}' extension")
                    # Create dynamical extension
                    qsrclist_vt.add_dynamical_hdu("FINDCH_*", suffix=seq)
                
                    # Initialize number of rows in table
                    qsrclist_vt.init_bintable(len(tab), ext=ext_name)
                
                    bin_tab = qsrclist_vt._fits_product[ext_name]
                
                    # Fill binary table column by column
                    for col_name, col_data in tab.columns.items():
                        log.debug(f"Processing column {col_name}")
                
                        if col_name not in bin_tab.columns.names:
                            log.warning(
                                f"Ignoring column '{col_name}' as it does not exist "
                                f"in FITS model for extension {ext_name}"
                            )
                            continue
                
                        qsrclist_vt.fill_bintable_col(col_name, col_data, ext=ext_name)
                
                    # Fill headers
                    # Remove some keywords
                    for k in ['SIM_ID', 'NPCKTS', 'DPACKETTIMES', 'SEQ', 'VHFNOBSNUMBER', 'MSSGTYPE', 'VHFIOBSTYPE']:
                        hdr.pop(k)
                    fill_headers(fits_template=qsrclist_vt, keywords_dict={ext_name:hdr})
            
            # Save reformatted QSRCLIST_VT
            qsrclist_fname = fits_dir/f'{sim_id}_qsrclist_vt.fits'
            qsrclist_vt.writeto(qsrclist_fname, overwrite=True, checksum=True)
        
            hand = vtac.handler.QuickPositionHandler(
                burst_id=sim_id, mode="local", cat_list=["PS1DR1", "SDSS12", "LSDR10"],
                qsrclist_vt_fname=qsrclist_fname,
            )
            hand.launch_processing()
            hand.create_qpo_vt(
                mode="local",
                json_product_descriptor_path="/Users/palmerio/SVOM_pipeline/json-product-descriptor/",
            )
            qpo_vt_fname = fits_dir/f'{sim_id}_qpo_vt.fits'
            hand.qpo_vt.writeto(qpo_vt_fname, overwrite=True, checksum=True)
        except Exception as exc:
            log.critical(f"Failed to process simulation {sim_id} because {exc}.\nMoving on to next simulation")
        i += 1

2024-01-22 16:06:43 -    INFO - [1990908818.py:  2 -   <module>()] - Processing simulations for case: bright_case1
2024-01-22 16:06:43 -    INFO - [1990908818.py:  8 -   <module>()] - ##################################################
2024-01-22 16:06:43 -    INFO - [1990908818.py:  9 -   <module>()] - Progress: 0.0 %
2024-01-22 16:06:43 -    INFO - [1990908818.py: 10 -   <module>()] - ##################################################
2024-01-22 16:06:43 -    INFO - [1990908818.py: 11 -   <module>()] - Processing simulation 0000001
2024-01-22 16:06:43 -    INFO - [handler.py:761 - get_product_template()] - Fetching template for QSRCLIST_VT
2024-01-22 16:06:43 -   DEBUG - [handler.py:763 - get_product_template()] - Using local template
2024-01-22 16:06:43 -    INFO - [fits_from_model.py:131 - _read_from_local()] - Reading JSON schema from /Users/palmerio/SVOM_pipeline/json-product-descriptor/data/products/json/QSRCLIST_VT.json
2024-01-22 16:06:43 -    INFO - [fits_from_model.py:140 - _

2024-01-22 16:06:44 -   DEBUG - [handler.py:176 - extract_sequences_to_process()] - Found ['R0', 'B0', 'R1', 'B1', 'R2', 'B2', 'R3', 'B3'] sequences to process
2024-01-22 16:06:44 -    INFO - [handler.py:135 -    summary()] - Handler is initialized with the following data:
burst_id: 0000001
catalogs: ['PS1DR1', 'SDSS12', 'LSDR10']
Existing QPO_MXT: True
Sequences to be processed found in QSRCLIST_VT: ['R0', 'B0', 'R1', 'B1', 'R2', 'B2', 'R3', 'B3']

2024-01-22 16:06:44 -    INFO - [handler.py:290 - launch_processing()] - Starting processing of sequence: R0
2024-01-22 16:06:44 -    INFO - [processor.py:509 - sequence_to_csv()] - Extracting data from HDU and converting to CSV file for sequence: R0
2024-01-22 16:06:44 -    INFO - [processor.py:111 - process_sequence()] - Processing sequence R0 with catalogs: ['PS1DR1', 'SDSS12', 'LSDR10']
2024-01-22 16:06:44 -    INFO - [crossmatch.py:127 - xmatch_with_cds_catalog()] - Sending crossmatch request to CDS for catalog PS1DR1 with radius 2.0 a

/Users/palmerio/SVOM_pipeline/VTAC_pipeline/vtac/catalogs.py:275: RuntimeWarning: invalid value encountered in log10
  tab[f"{band}mag"] = 22.5 - 2.5 * np.log10(tab[f"flux_{band}"])


2024-01-22 16:06:52 -    INFO - [processor.py:132 - process_sequence()] - Found 46 new sources (out of 236) not in catalog LSDR10 for sequence R0
2024-01-22 16:06:52 -    INFO - [processor.py:1119 - calc_delta_mag_with_cat()] - Calculating delta magnitude compared to catalogs: ['PS1DR1', 'SDSS12', 'LSDR10']
2024-01-22 16:06:52 -    INFO - [processor.py:1360 - calc_xflag()] - Calculating crossmatch flag XFLAG for band: R
2024-01-22 16:06:52 -    INFO - [processor.py:194 - combine_sequence()] - There is no 'COMBINED' table yet, creating it from sequence R0.
2024-01-22 16:06:52 -    INFO - [processor.py:1242 - create_ra_dec_cols()] - Assigning RA and DEC columns
2024-01-22 16:06:52 -    INFO - [processor.py:1317 - clean_xflag_nans()] - Cleaning NaNs in columns: ['XFLAG_R0']
2024-01-22 16:06:52 -    INFO - [processor.py:1161 - calc_variability_between_seq()] - Calculating magnitude variation flag VFLAG for sequences: ['R0']
2024-01-22 16:06:52 -    INFO - [processor.py:1166 - calc_variabil

/Users/palmerio/SVOM_pipeline/VTAC_pipeline/vtac/catalogs.py:275: RuntimeWarning: invalid value encountered in log10
  tab[f"{band}mag"] = 22.5 - 2.5 * np.log10(tab[f"flux_{band}"])


...

2024-01-22 16:33:40 -    INFO - [fits_validator.py:123 - check_expected_value()] - Only enumeration is supported for the validation of the expected values
For input keyword OBS_ID with value 4294967295
2024-01-22 16:33:40 -    INFO - [fits_validator.py:123 - check_expected_value()] - Only enumeration is supported for the validation of the expected values
For input keyword OBS_NUM with value 16777215
2024-01-22 16:33:40 -    INFO - [fits_validator.py:123 - check_expected_value()] - Only enumeration is supported for the validation of the expected values
For input keyword OBS_TYPE with value 255
2024-01-22 16:33:40 -    INFO - [fits_validator.py:123 - check_expected_value()] - Only enumeration is supported for the validation of the expected values
For input keyword MXT_RA with value None
2024-01-22 16:33:40 -    INFO - [fits_validator.py:123 - check_expected_value()] - Only enumeration is supported for the validation of the expected values
For input keyword MXT_DEC with value None
2024-01

2024-01-22 16:33:44 -    INFO - [builder.py:154 - fill_keyword()] - TABLE_COLUMN
2024-01-22 16:33:44 -    INFO - [1990908818.py: 21 -   <module>()] - Processing sequence s1 of band B
2024-01-22 16:33:44 -    INFO - [builder.py:151 - fill_keyword()] - read keyword ORIGIN
2024-01-22 16:33:44 -    INFO - [builder.py:151 - fill_keyword()] - read keyword TELESCOP
2024-01-22 16:33:44 -    INFO - [builder.py:151 - fill_keyword()] - read keyword INSTRUME
2024-01-22 16:33:44 -    INFO - [builder.py:151 - fill_keyword()] - read keyword CREATOR
2024-01-22 16:33:44 -    INFO - [builder.py:151 - fill_keyword()] - read keyword CARD
2024-01-22 16:33:44 -    INFO - [builder.py:151 - fill_keyword()] - read keyword PROGRAM
2024-01-22 16:33:44 -    INFO - [builder.py:151 - fill_keyword()] - read keyword PRDM_VER
2024-01-22 16:33:44 -    INFO - [builder.py:151 - fill_keyword()] - read keyword GLDM_VER
2024-01-22 16:33:44 -    INFO - [builder.py:151 - fill_keyword()] - read keyword PROC_VER
2024-01-22 16:3

/Users/palmerio/SVOM_pipeline/VTAC_pipeline/vtac/catalogs.py:275: RuntimeWarning: divide by zero encountered in log10
  tab[f"{band}mag"] = 22.5 - 2.5 * np.log10(tab[f"flux_{band}"])
/Users/palmerio/SVOM_pipeline/VTAC_pipeline/vtac/catalogs.py:275: RuntimeWarning: invalid value encountered in log10
  tab[f"{band}mag"] = 22.5 - 2.5 * np.log10(tab[f"flux_{band}"])


2024-01-22 16:33:52 -    INFO - [processor.py:132 - process_sequence()] - Found 21 new sources (out of 210) not in catalog LSDR10 for sequence R0
2024-01-22 16:33:52 -    INFO - [processor.py:1119 - calc_delta_mag_with_cat()] - Calculating delta magnitude compared to catalogs: ['PS1DR1', 'SDSS12', 'LSDR10']
2024-01-22 16:33:52 -    INFO - [processor.py:1360 - calc_xflag()] - Calculating crossmatch flag XFLAG for band: R
2024-01-22 16:33:52 -    INFO - [processor.py:194 - combine_sequence()] - There is no 'COMBINED' table yet, creating it from sequence R0.
2024-01-22 16:33:52 -    INFO - [processor.py:1242 - create_ra_dec_cols()] - Assigning RA and DEC columns
2024-01-22 16:33:52 -    INFO - [processor.py:1317 - clean_xflag_nans()] - Cleaning NaNs in columns: ['XFLAG_R0']
2024-01-22 16:33:52 -    INFO - [processor.py:1161 - calc_variability_between_seq()] - Calculating magnitude variation flag VFLAG for sequences: ['R0']
2024-01-22 16:33:52 -    INFO - [processor.py:1166 - calc_variabil

AttributeError: 'tuple' object has no attribute 'tb_frame'

In [34]:
log = logging.getLogger(__name__)
log.handlers

[]

In [47]:
l1 = {
    'a':[1,2,3],
    'b':[1,2,4],
}
l2 = ['a','b']

from itertools import product
l0 = [(k, v) for k,v in zip([l1.keys(),l1.values())]


<function logging.config.dictConfig(config)>

In [86]:
x = lambda r: r.name == 'root'

In [93]:
log.parent

<RootLogger json-product-generator.fits_builder (INFO)>

In [95]:
tab = Table({'x':np.arange(10)})

In [96]:
tab.write('~/Desktop/delete.txt', format='ascii.tab', overwrite=True)

In [ ]:
tab.meta['comment'] = "# test"